In [10]:
%load_ext autoreload
%autoreload 2
%matplotlib inline  

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.offline as pl
pl.init_notebook_mode(connected=True)
import plotly.graph_objs as go

from datetime import datetime, timedelta
import parseIntervalFiles as pif
import parseActivityFiles as paf
#pun intended :)
import consolidateFiles as cf
import datacleaning as cl
import dataviz as dv

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [11]:
verbose = True

PATH = "C:\\Users\\ju\\GDrive\\Projects\\HeRV\\Data\\"
RAW = PATH + "Raw"

In [12]:
file = PATH + "PreProcessed\\sessions.xlsx"
df = pd.read_excel(file)
df.sample(5)

activity  beatscount  duration           hf       hfnu  \
236  focused-active        1913      1528   424.785132  18.423927   
436             eat        3623      2701   173.556304  21.220596   
81   focused-active        3778      2520   305.186086  26.886796   
419             eat        1435      1207  9705.955863  65.352806   
233             eat         589       391   396.802627  17.519016   

              lf     lf_hf       lfnu        mhr        mrri   ...     \
236  1880.831595  4.427725  81.576073  74.167713  817.078411   ...      
436   644.310951  3.712403  78.779404  79.203816  762.747171   ...      
81    829.891848  2.719298  73.113204  88.344377  682.902859   ...      
419  5145.672441  0.530156  34.647194  78.653690  819.043902   ...      
233  1868.179813  4.708083  82.480984  90.405891  669.521222   ...      

     posture removed_artifacts       rmssd        sdnn               start  \
236      sit                 1   48.286621   81.006877 2017-11-01 18:49:14   
436      sit                 0   41.899943   62.458526 2018-01-01 21:09:24   
81       sit                 0   27.574666   51.561401 2017-10-15 01:45:00   
419      sit                72  195.262338  172.544644 2017-12-26 21:30:36   
233      sit                 0   31.094682   64.314292 2017-11-01 15:47:14   

                   stop   total_power user          vlf  sess_id  
236 2017-11-01 19:14:42   4017.437225    1  1711.820497      236  
436 2018-01-01 21:54:25   1382.034134    5   564.166878      436  
81  2017-10-15 02:27:00   1653.704861    0   518.626927       81  
419 2017-12-26 21:50:43  16372.745221    5  1521.116917      419  
233 2017-11-01 15:53:45   2949.450401    1   684.467961      233  

[5 rows x 23 columns]

In [13]:
len(df)

458

## Plotting random examples of RR time series for each type of activity

In [6]:
for act in df['activity'].unique():
    v = df[df['activity'] == act].sample(1)
    print('---------------- ', act, ' ---------------')
    for i in range(1):
        print('USER: ', v.iloc[i]['user'])
        dv.plot_sess_rr(v.iloc[i], RAW, act)

----------------  focused-active  ---------------
USER:  1


----------------  leisure  ---------------
USER:  4


----------------  eat  ---------------
USER:  0


----------------  movement  ---------------
USER:  0


----------------  sleep  ---------------
USER:  0


----------------  rest-passive  ---------------
USER:  0


----------------  rest-active  ---------------
USER:  0


----------------  household-chores  ---------------
USER:  2


----------------  focused-passive  ---------------
USER:  0


----------------  exercise  ---------------
USER:  0


### Removing outliers from frequency domain

In [15]:
dfc = df[df['hf'] < 4000]
print(len(df) - len(dfc))
print(len(dfc))

54
404


In [16]:
dfc = dfc[dfc['lf'] < 7000]
print(len(dfc))

403


## Plotting features summary for each type of session (users 0, 1 and 2)
---

In [19]:
for user in range(3):    
    
    print('--------------------------------------------------------------------------------------------')
    print('')
    print('---------------------------------------- user: ', user, ' ----------------------------------------')
    print('')
    print('--------------------------------------------------------------------------------------------')
    
    for feat in cl.features_all:        
        dv.boxplot_compare(dfc[dfc['user'] == user], feat, groupby='activity', min_examples=2)

--------------------------------------------------------------------------------------------

---------------------------------------- user:  0  ----------------------------------------

--------------------------------------------------------------------------------------------


--------------------------------------------------------------------------------------------

---------------------------------------- user:  1  ----------------------------------------

--------------------------------------------------------------------------------------------


--------------------------------------------------------------------------------------------

---------------------------------------- user:  2  ----------------------------------------

--------------------------------------------------------------------------------------------


## Plotting features summary for each user (sitting activities combined)
---

In [17]:
for feat in ['rmssd', 'pnn50', 'hfnu', 'lfnu', 'lf_hf']:
    dv.boxplot_compare(dfv, feat, groupby='user', min_examples=2)

In [16]:
ulist = [0,1,2,4,5,6]
alist = ['leisure','focused-passive', 'focused-active','rest-passive','rest-active']
dfv = dfc[(dfc.posture == 'sit') & (dfc.user.isin(ulist)) & dfc.activity.isin(alist)]

for feat in cl.features_all:
    dv.boxplot_compare(dfv, feat, groupby='user', min_examples=2)
    